# Deliverable 3. Create a Travel Itinerary Map

----

1. Create a folder called `Vacation_Itinerary` to store all the files for this deliverable.

2. Download the `Vacation_Itinerary_starter_code.ipynb` file into your `Vacation_Itinerary` folder and rename it `Vacation_Itinerary.ipynb`.

3. Make sure the initial dependencies and the Geoapify API key are imported.

4. From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`.

5. Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

    * The point's size should be the maximum temperature for the city

    * The point's color should be the city's name

    * Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

6. From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

    > **Hint:** You will start and end the route in the same city, so the `vacation_start` and `vacation_end` DataFrames will be in the same city.

7. Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details.

8. Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`.

    > **Hint:** You'll use this DataFrame to create a map using GeoViews, so recall that the first column should be the longitude, and the second the latitude.

9. Use GeoViews to create a map that shows the four cities in the itinerary.

10. Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop.

    > **Hint:** You can note that the `mode` parameter is set to `drive`, you can play around with other modes as it's shown in [the "Travel modes" table](https://apidocs.geoapify.com/docs/routing/#api) in the Geoapify Routing API documentation.

11. Use the Geoapify Routing API to retrieve the route's directions for your itinerary.

12. From the JSON response, store the route's legs coordinates in a variable called `legs`.

13. Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude values into two Python lists named `longitude` and `latitude`.

14. Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`.

15. Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map.

16. Use the asterisk operator to display a composed plot that shows the itinerary's route over the map containing the cities. 

17. Save your map to the `Vacation_Itinerary` folder as `WeatherPy_travel_map.png`.

---

## Make sure the initial dependencies and the Geoapify API key are imported

In [1]:
# Dependencies and Setup
import geoviews as gv
import hvplot.pandas
import pandas as pd
import requests

# Turn off warning messages
import warnings
warnings.filterwarnings("ignore")

# Import API key
from config import geoapify_key

## From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`

In [3]:
# Read the WeatherPy_vacation.csv into a DataFrame
vacation_df = pd.read_csv("../Vacation_Search/WeatherPy_vacation.csv")

# Display sample data
vacation_df.head(5)

Unnamed: 0           City Country  Max Temp weather description      Lat  \
0           1        Rikitea      PF     76.87     overcast clouds -23.1203   
1           6   Puerto Ayora      EC     76.96       broken clouds  -0.7393   
2           9  Mar Del Plata      AR     83.82    scattered clouds -38.0023   
3          12           Atar      MR     77.27           clear sky  20.5169   
4          15         Neiafu      TO     75.88          few clouds -18.6500   

        Lng                            Hotel Name  
0 -134.9692                  Chez Bianca & Benoit  
1  -90.3518  Hostal La Mirada De Solitario George  
2  -57.5575                         Nuevo Ostende  
3  -13.0499                            فندق سكليل  
4 -173.9833                 Port Wine Guest House

## Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

* The point's size should be the maximum temperature for the city

* The point's color should be the city's name

* Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

In [4]:
# Configure the map plot
map_plot = vacation_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 700,
    frame_height = 500,
    size = "Max Temp",
    scale = 1,
    color = "City",
    hover_cols = ["Hotel Name", "Country",'weather description']
)

# Display the map
map_plot

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country,weather description)

## From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

In [129]:
# Create DataFrames for each city by filtering the 'vacation_df' using the loc method
vacation_start = vacation_df.loc[vacation_df["City"]=="Cape Town"]# Sao Felix Do Xingu
vacation_end = vacation_start
vacation_stop1 = vacation_df.loc[vacation_df["City"]=="Port Elizabeth"] # Alta Floresta
vacation_stop2 = vacation_df.loc[vacation_df["City"]=="Hermanus"] # Ariquemes
vacation_stop3 = vacation_df.loc[vacation_df["City"]=="Saldanha"] # Humatia


## Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details

In [130]:
# Use the Pandas concat function to create a new DataFrame to store the itinerary details.
itinerary_df =pd.concat([vacation_start, vacation_stop1 , vacation_stop2 , vacation_stop3 , vacation_end] )

# Display sample data
itinerary_df

Unnamed: 0            City Country  Max Temp weather description      Lat  \
15          63       Cape Town      ZA     82.11           clear sky -33.9258   
7           25  Port Elizabeth      ZA     79.11          light rain -33.9180   
6           24        Hermanus      ZA     76.80       broken clouds -34.4187   
86         420        Saldanha      ZA     80.65    scattered clouds -33.0117   
15          63       Cape Town      ZA     82.11           clear sky -33.9258   

        Lng        Hotel Name  
15  18.4232   Townhouse Hotel  
7   25.5701   Waterford Hotel  
6   19.2345  Aloe guest house  
86  17.9442       Hoedjesbaai  
15  18.4232   Townhouse Hotel

## Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`

In [131]:
# Create a Pandas DataFrame to store the latitude and longitude for each city in the itineray
waypoints_df =itinerary_df[["Lng","Lat"]].copy() # YOUR CODE HERE

# Display sample data
waypoints_df

Lng      Lat
15  18.4232 -33.9258
7   25.5701 -33.9180
6   19.2345 -34.4187
86  17.9442 -33.0117
15  18.4232 -33.9258

## Use GeoViews to create map that shows the four cities in the itinerary

In [132]:
# Configure the map plot by using the itineraty_df
waypoints_map = waypoints_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 700,
    frame_height = 500,
    scale = 1,
    hover_cols = ["Lng", "Lat"]
)

In [133]:
# Display the route_map
waypoints_map

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]

## Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop

In [134]:
# Set parameters to trace the route
radius = 5000
params = {
    "mode":"drive",
    "apiKey": geoapify_key,
}

In [135]:
# Set an empty waypoints String variable
waypoints = ""

# Iterate through the route_df DataFrame to define the waypoints
for index, row in waypoints_df.iterrows():
    waypoints = waypoints + str(row["Lat"]) + "," + str(row["Lng"]) + "|"

# Delete the last character from the string
waypoints = waypoints[:-1]

# Add the waypoints to the params dictionary
params["waypoints"] = waypoints

# Display the params dictionary
params

{'mode': 'drive',
 'apiKey': '475ec20738e24fc08959ecfaa24e12fe',
 'waypoints': '-33.9258,18.4232|-33.918,25.5701|-34.4187,19.2345|-33.0117,17.9442|-33.9258,18.4232'}

## Use the Geoapify Routing API to retrieve the route's directions for your itinerary

In [136]:
# Set up the base URL for the Geoapify Places API.
base_url = "https://api.geoapify.com/v1/routing"

# Make request and retrieve the JSON data by using the params dictionaty
route_response = requests.get(base_url, params=params)

# Convert the API response to JSON format
route_response = route_response.json()


## From the JSON response, store the route's legs coordinates in a variable called `legs`

In [147]:
# Fetch the route's legs coordinates from the JSON reponse
legs = route_response['features'][0]['geometry']['coordinates']
legs

[[[18.422919, -33.926062],
  [18.423419, -33.926432],
  [18.424143, -33.926975],
  [18.424191, -33.927011],
  [18.424246, -33.926958],
  [18.424363, -33.926852],
  [18.424752, -33.926502],
  [18.424801, -33.926451],
  [18.425158, -33.926097],
  [18.425239, -33.926021],
  [18.425328, -33.925939],
  [18.425819, -33.925439],
  [18.425982, -33.925287],
  [18.425999, -33.925272],
  [18.426023, -33.925239],
  [18.426032, -33.925206],
  [18.426033, -33.925174],
  [18.426024, -33.925115],
  [18.42597, -33.924961],
  [18.425935, -33.924843],
  [18.425938, -33.924767],
  [18.425962, -33.924705],
  [18.42624, -33.924393],
  [18.426292, -33.924309],
  [18.426368, -33.924175],
  [18.426457, -33.924206],
  [18.426587, -33.924246],
  [18.426706, -33.924283],
  [18.428482, -33.924882],
  [18.430244, -33.925457],
  [18.431324, -33.92583],
  [18.431934, -33.925989],
  [18.432191, -33.926029],
  [18.433424, -33.92609],
  [18.433557, -33.926103],
  [18.433688, -33.926137],
  [18.433811, -33.926185],
  [18

## Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude value into two Python lists names `longitude` and `latitude`

In [156]:
# Create and empty list to store the longitude of each step
# YOUR CODE HERE
longitude=[]
# Create and empty list to store the latitude of step
# YOUR CODE HERE
latitude=[]
# Loop through the legs coordinates to fetch the latitude and longitude for each step
for index in legs:
    for coordinates in index:
    # Get latitude and longitude from DataFrame.
        latitude.append(coordinates[1])
        longitude.append(coordinates[0])


## Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`

In [157]:
# Create an empty DataFrame to store the steps' coordinates
route_df = pd.DataFrame(columns=['lat','lon'])

# Add the steps' longitude and latitude from each step as columns to the DataFrame
route_df['lat']=latitude
route_df['lon']=longitude
# Display sample data
route_df.head(5)

lat        lon
0 -33.926062  18.422919
1 -33.926432  18.423419
2 -33.926975  18.424143
3 -33.927011  18.424191
4 -33.926958  18.424246

##  Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map

In [158]:
# Configure the route path by using the GeoViews' Path function
route_path = gv.Path(route_df, kdims=['lon','lat'])


In [159]:
# Display a composed plot by using the route_map and route_path objects
waypoints_map * route_path.options(color= "red", line_width=3)

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]
   .Path.I   :Path   [lon,lat]